This Jupyter notebook will use the SEAScope viewer and SEAScope Python bindings to retrieve inputs data
* author: Lucile Gaultier, OceanDataLab
* date: 2022-10-12

To install SEAScope, follow the instructions on the [SEAScope website](https://seascope.oceandatalab.com/) and demonstrated in our ["SEAScope How To" YouTube playlist](https://www.youtube.com/playlist?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK).

To install the required Python packages, follow the instructions on https://pypi.org/project/SEAScope-env-OTC2023.
* **Windows** users can also follow the [Complete SEAScope install with Python modules for OTC23 on Windows](https://youtu.be/uomHRQPgqb8?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=3&t=132s) video on YouTube
* **macOS** users can also follow the [Installing SEAScope Python modules for OTC23 on macOS](https://youtu.be/w5f0ow6iPOY?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=6) video on YouTube

# Derive geostrophic velocity from mapped SSH

The geostrophic balance is valid when the pressure gradient force is balanced by the Coriolis effect. It is a simplification of the Navier Stokes Equation assuming that:
* The circulation is 2D (vertical velocity very small)
* The acceleration is small (steady state)
* Viscosity is negligible

This balance is valid at large scales (hundreds of km) and away from the equator.</br>
The geostrophic component can be derived from the Sea Surface Height (SSH) also called Absolute Dynamic Topography (ADT) in SEAScope catalog:
$$ u = -\frac{g}{f} \frac{\partial (SSH)}{\partial y}$$
$$ v = \frac{g}{f} \frac{\partial (SSH)}{\partial x}$$
with $f$ the Coriolis parameter, and $g$ the gravitation parameter.

In this notebook, we will use the mapped SSH (or ADT) from the CMEMS geostrophic product to compute geostrophic current.
This SSH comes from altimeter remote sensing observations that have been optimally interpolated.

This notebook will teach you how to:
* Import data from SEAScope
* Export data to SEAScope
* Derive geostrophic velocity from SSH

<div class="alert alert-warning">
<strong>This notebook uses the following data collection:</strong>

* directory: `cmems_008_046`, label: `CMEMS sea level NRT observations`

Check that you have it in your SEAScope catalogue before continuing with this notebook.<br>
This collection was included in the first data package you downloaded (the [light_samples.zip](https://ftp.odl.bzh/odl/events/otc23/light_samples.zip)).

And it can be downloaded at https://ftp.odl.bzh/odl/events/otc23/cmems_008_046.zip

To learn how to add data to SEAScope, you can watch one of the following YouTube videos:
* [How to add data to SEAScope on **Windows**](https://youtu.be/TsJSg7V7WNU?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=2)
    * or the "Add data to SEAScope" chapter of [How to add data to SEAScope on **Windows**](https://youtu.be/uomHRQPgqb8?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=3&t=40s)
* [How to add data to SEAScope on **macOS**](https://youtu.be/s5X3ewpmcuw?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=5)
* [How to add data to SEAScope on **Linux**](https://youtu.be/3ZAzgl3v2lo?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=8)
</div>

In [ ]:
# Import necessary modules
%matplotlib inline
import matplotlib.pyplot as plt
import numpy
import os

# Create once the collection for this notebook
collection_id = None
import SEAScope.lib.utils
SEAScope.lib.utils.init_ids(20, 2000)

## 1. Find the data of interest in SEAScope

##### Select and locate the data in the SEAScope viewer

1. In the "Catalogue" (the panel on the right), select 
    * collection `CMEMS sea level NRT observation`, variable `absolute dynamic topography`
2. Pick a date where you have data available (highlighted in green in the timeline)
    * The 1<sup>st</sup> of January 2015 should be good
3. Zoom in an area where the geostrophic balance is valid
    * The Agulhas region is a good area
4. Tell SEAScope to use bilinear interpolation when rendering this data by:
    1. clicking on the cogwheel to the right of `CMEMS sea level NRT observation: absolute dynamic topography`, in the "Display data" panel, then
    2. selecting "Bilinear" under the "Filtering" section

## 2. Get data from the SEAScope viewer using the python bindings

##### Extract the data from SEAScope

1. Zoom-in to properly see the structures in the data (the resolution of the extraction depends on the zoom level)
2. Draw a polygon over the region you want to extract:
    1. Start drawing by clicking on the 3<sup>rd</sup> button to the right of the pen icon in the toolbar or by hitting the <kbd>P</kbd> key
    2. Place the corners of the polygon by left-clicking on the globe
    3. Once all the corners placed, hit the <kbd>Enter</kbd> or <kbd>Return</kbd> key to commit your polygon
3. Select the polygon you just created by clicking on it
4. Extract the data intersecting that polygon by clicking on the extract button in the "Selected annotation" panel

You can also watch the [How to export data from SEAScope](https://youtu.be/nADgZQ8o31s) video on YouTube.

##### Load the extracted data

In [ ]:
#Load data directly from viewer memory
from SEAScope.lib import get_extracted_data
extractions = get_extracted_data()

# Sort extracted granules by ascending time
time_sorted_extractions = dict(sorted(extractions.items(), key=lambda _: _[1]['meta']['start']))

##### Identify CMEMS sea level SSH extracted granules

In [ ]:
# Keep a list of indices for granules whose name matches the CMEMS SSH data
k_ssh = []
for k, (granule_path, granule_info) in enumerate(extractions.items()):
    granule_name = os.path.basename(granule_path)
    if 'phy_l4' in granule_name:
        k_ssh.append(k)

    # Print extracted granule data 
    print(f'{k} - {granule_name}')
    print('\n'.join([f'\t{_}' for _ in granule_info['data']]))

if len(k_ssh) == 0:
    print('Wrong collections selected, go back to SEAScope and select "CMEMS sea level NRT observations" collection, "absolute dynamic topography" variable')

##### Select the granules to analyze

In [ ]:
# If several granules have been selected, select the one you want to process
kt = 0 # ⚠️ You can adapt if you have several granules imported

granule_names_list = list(time_sorted_extractions.keys())
granule_name = granule_names_list[k_ssh[kt]]
extraction = time_sorted_extractions[granule_name]

ssh = extraction['data']['adt']

# Spatial coverage will be the mesh of the polygon used to perform the extraction
# It is available in the "gcps" metadata for each extraction
gcps = extraction['meta']['gcps']

# Make sure the result is reset
granule_id = None

## 3. Get coordinates and plot SSH

In [ ]:
# Get longitudes and latitudes from gcps
lon = [x['lon'] for x in gcps]
lat = [x['lat'] for x in gcps]

# Mask invalid SSH values
ssh[abs(ssh) > 100] = numpy.nan

from SEAScope.lib.utils import get_lonlat
lon2D, lat2D = get_lonlat(extraction, numpy.shape(ssh))

In [ ]:
plt.pcolormesh(lon2D, lat2D, ssh, cmap='jet')
plt.colorbar() 
plt.title('SSH')

## 4. Compute geostrophic current

Compute the surface oceanic currents assuming geostrophic balance:
$$ u = -\frac{g}{f} \frac{\partial (SSH)}{\partial y}$$
$$ v = \frac{g}{f} \frac{\partial (SSH)}{\partial x}$$

##### Define geophysical constants

In [ ]:
# Gravitation parameter
constant_g = 9.81
# Coriolis parameter
constant_f0 = 2 * 7.2921e-5
# Convert degrees to meters
degtom = 111.11e3

##### Compute geostrophic velocities using a central scheme

**<span style="color:red">Choose the differential discretization number `num_diff` for a centered scheme</span>**

In [ ]:
num_diff = 2  # Usual value is 2
num_centered = num_diff // 2

# Initialize null matrices
ugeo = numpy.full(numpy.shape(ssh), 0.)
vgeo = numpy.full(numpy.shape(ssh), 0.)

# Compute g/f
goverf = constant_g / (constant_f0 * numpy.sin(numpy.deg2rad(lat2D)))

# Compute derivatives
dsshy = ssh[num_diff:, :] - ssh[:-num_diff, :]
dsshx = ssh[:, num_diff:] - ssh[:, :-num_diff]
dlonx = (
    (lon2D[:,num_diff:] - lon2D[:,:-num_diff])
    * numpy.cos(numpy.deg2rad(lat2D[:, num_centered:-num_centered]))
    * degtom
)
dlaty = (lat2D[num_diff:,:] - lat2D[:-num_diff,:]) * degtom

# Compute geostrophic velocities
ugeo[num_centered:-num_centered, :] = -goverf[num_centered:-num_centered, :] * dsshy / dlaty
vgeo[:, num_centered:-num_centered] = goverf[:, num_centered:-num_centered] * dsshx / dlonx

# Mask invalid values
ugeo = numpy.ma.array(ugeo, mask=(ssh.mask | (abs(ugeo)>10)))
vgeo = numpy.ma.array(vgeo, mask=(ssh.mask | (abs(vgeo)>10)))

##### Plot the computed velocity

In [ ]:
norm = numpy.sqrt(ugeo**2 + vgeo**2)
fig = plt.figure(figsize=(16,10))
C = plt.pcolormesh(lon2D, lat2D, norm, cmap='jet')  
ss = 10
Q = plt.quiver(lon2D[::ss, ::ss], lat2D[::ss, ::ss], 
               numpy.clip(ugeo[::ss,::ss], -2, 2),
               numpy.clip(vgeo[::ss,::ss], -2, 2))
qk = plt.quiverkey(Q, 0.5, 0.98, 2, r'$2 \frac{m}{s}$', labelpos='W',
                                fontproperties={'weight': 'bold'})
plt.colorbar(C) 
plt.title('Geostrophic current speed')

## 5. Export data back to SEAScope

In [ ]:
import datetime

from SEAScope.lib.utils import create_collection, create_variable
from SEAScope.lib.utils import create_granule, set_field

**Define Collection: <br>
A granule has to belong to a collection<br>
<span style="color:red">You may choose a name for the collection `collection_name`</span>**

In [ ]:
if collection_id is None:
    # Collection
    collection_name = 'User - Geostrophic current' # ⚠️ You can choose your collection name
    # Create collection
    collection_id, collection = create_collection(collection_name)
print(collection_id)

**Define the granule that will hold the results. Granules are defined by their spatial and temporal coverage**

In [ ]:
# Reuse the temporal coverage of the CMEMS SSH input granule
# - Start time of granule 
dtstart = extraction['meta']['start']
# - End time of granule 
dtstop = extraction['meta']['stop']

# Create granule
if granule_id is None:
    granule_id, granule = create_granule(collection_id, gcps, dtstart, dtstop)

**The granule will contain each result matrix as what we call a "field"<br>
<span style="color:red">You may choose a name for each field: `field_name_u` and `field_name_v`</span></br>**

In [ ]:
# Attach data fields to the granule
field_name_u = 'u_geo' # ⚠️ You can choose your field name
field_name_v = 'v_geo' # ⚠️ You can choose your field name
set_field(granule, field_name_u, ugeo)
set_field(granule, field_name_v, vgeo)

**Next you need to tell SEAScope what to display: this is done by defining a "variable" which can be composed of one, two or three fields.<br>
When a variable has two fields, these are considered to be the meridional and zonal components of a vector field.** <br>
**<span style="color:red">You may choose a name for each variable you want to display: `variable_name_u`, `variable_name_u` and `variable_name_norm`</span>**

In [ ]:
# Create a variable for the horizontal component
variable_name_u = 'Zonal geostrophic current'  # ⚠️ You can choose your label name
tmp = create_variable(collection,variable_name_u, [field_name_u])
if tmp is not None:
    u_variable = tmp
else:
    print()
    raise Exception('See issues above')

# Create a variable for the vertical component 
variable_name_v =  'Meridional geostrophic current'  # ⚠️ You can choose your label name
tmp = create_variable(collection,variable_name_v, [field_name_v])
if tmp is not None:
    v_variable = tmp
else:
    print()
    raise Exception('See issues above')

# Create a variable for the complete vector
variable_name_norm = 'Geostrophic current speed'  # ⚠️ You can choose your label name
tmp = create_variable(collection, variable_name_norm, [field_name_u, field_name_v])
if tmp is not None:
    norm_variable = tmp
else:
    print()
    raise Exception('See issues above')

**It is also possible to tell SEAScope how to display variables: the following cell shows how to set some rendering options**<br>

In [ ]:
# Rendering configuration for the horizontal component
u_rcfg = u_variable['rendering']
u_rcfg['min'] = numpy.min(ugeo)
u_rcfg['max'] = numpy.max(ugeo)
u_rcfg['colormap'] = 'jet'
u_rcfg['zindex'] = 0.3
u_rcfg['filterMode'] = 'NEAREST'

# Rendering configuration for the vertical component
v_rcfg = v_variable['rendering']
v_rcfg['min'] = numpy.min(vgeo)
v_rcfg['max'] = numpy.max(vgeo)
v_rcfg['colormap'] = 'jet'
v_rcfg['opacity'] = 0.3
v_rcfg['filterMode'] = 'NEAREST'

# Rendering configuration for the complete vector
norm_rcfg = norm_variable['rendering']
norm_rcfg['min'] = 0.0
norm_rcfg['max'] = 2.5
norm_rcfg['colormap'] = 'jet'

**Finally, send the collection, granule and variable to SEAScope**

In [ ]:
hostname = '127.0.0.1'
port = 11155
with SEAScope.upload.connect(hostname, port) as link:
    # Upload the collection first (remember: a granule cannot exist before its collection has been uploaded!)
    SEAScope.upload.collection(link, collection)

    # Then the granule
    SEAScope.upload.granule(link, granule)

    # Now SEAscope has access to the data, all that remains is telling the application what and how it should display them, by uploading the variable definition
    SEAScope.upload.variable(link, u_variable)
    SEAScope.upload.variable(link, v_variable)
    SEAScope.upload.variable(link, norm_variable)
    
    SEAScope.upload.rendering_config(link, u_rcfg)
    SEAScope.upload.rendering_config(link, v_rcfg)
    SEAScope.upload.rendering_config(link, norm_rcfg)

## 6. Visualize your geostrophic current in the SEAScope viewer

Your new collection should have appeared in the "Catalogue"
* Your collection is the `collection_name` you have defined previously
* Your variables are the `variable_name` you have defined previously
* Select the data you have just exported
* Select the `CMEMS sea level NRT observations` collection, variable `geostrophic current from MADT`
* Play with transparency to compare your result with the official CMEMS geostrophic velocity: you might notice some difference in filtering and strength as a more complex algorithm is applied in the official CMEMS geostrophic velocity product

**You can still change the rendering configuration using the notebook, just remember to send the modified configuration to SEAScope <br />
<span style="color:red"> You can play with min, max values, the colormap ... and check how the rendering changes on SEAScope</span>**

In [ ]:
norm_rcfg['min'] = 0
norm_rcfg['max'] = 2.0
norm_rcfg['colormap'] = 'ylgnbu'

with SEAScope.upload.connect(hostname, port) as link:
    SEAScope.upload.rendering_config(link, norm_rcfg)